# Covid 19 Data modelling in R

https://docs.idmod.org/projects/emod-hiv/en/latest/model-overview.html

In [1]:
# Clean Environment
rm(list = ls())
gc()

used    (Mb) gc trigger (Mb) max used (Mb)
Ncells  567695 30.4 1229600    65.7  713200  38.1
Vcells 1064924  8.2 8388608    64.0 1820463  13.9

In [2]:
# Import needed libraries
library(covid19.analytics)
library(dygraphs)
library(writexl)
library(xts)
library(deSolve)
library(reshape2)

Loading required package: zoo


Attaching package: ‘zoo’


The following objects are masked from ‘package:base’:

    as.Date, as.Date.numeric




In [ ]:
KerasNNRegressor <- function(
  x = x,
  y = y,
  cutoff = .9,
  validation_split = 1 - cutoff,
  loss = 'mae',
  optimizer = optimizer_rmsprop(),
  batch_size = 128,
  activation = 'relu',
  finalactivation = 'sigmoid',
  numberOfHiddenLayers = 1,
  useBias = FALSE,
  l1.units = 20,
  l2.units = 10,
  l3.units = 5,
  l4.units = 4,
  l5.units = 2,
  dropoutRate = 0.2,
  epochs = 10,
  forceClassifier = FALSE
) {

  # Package
  library(keras)

  # Data
  all <- data.frame(cbind(y, x))

  # Setup
  train_idx <- 1:round(cutoff*nrow(all),0)
  x_train <- as.matrix(all[train_idx, -1])
  y_train <- as.matrix(all[train_idx, 1])
  x_test <- as.matrix(all[-train_idx, -1])
  y_test <- as.matrix(all[-train_idx, 1])

  # Check levels for response
  number.of.levels <- nrow(plyr::count(y_train))
  num_classes <- number.of.levels

  # To prepare this data for training we one-hot encode the
  # vectors into binary class matrices using the Keras to_categorical() function
  # y_train <- to_categorical(y_train, number.of.levels)
  # y_test <- to_categorical(y_test, number.of.levels)

  # Defining the Model
  if (numberOfHiddenLayers == 0) {
    model <- keras_model_sequential()
    model %>%
      layer_dense(
        units = 1,
        input_shape = c(ncol(x_train)),
        activation = finalactivation,
        use_bias = useBias)
    summary(model)
  } else if (numberOfHiddenLayers == 1) {
    model <- keras_model_sequential()
    model %>%
      layer_dense(units = l1.units, activation = activation, input_shape = c(ncol(x_train))) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = 1, activation = finalactivation)
    summary(model)
  } else if (numberOfHiddenLayers == 2) {
    model <- keras_model_sequential()
    model %>%
      layer_dense(units = l1.units, activation = activation, input_shape = c(ncol(x_train))) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l2.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = 1, activation = finalactivation)
    summary(model)
  } else if (numberOfHiddenLayers == 3) {
    model <- keras_model_sequential()
    model %>%
      layer_dense(units = l1.units, activation = activation, input_shape = c(ncol(x_train))) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l2.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l3.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = 1, activation = finalactivation)
    summary(model)
  } else if (numberOfHiddenLayers == 4) {
    model <- keras_model_sequential()
    model %>%
      layer_dense(units = l1.units, activation = activation, input_shape = c(ncol(x_train))) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l2.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l3.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l4.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = 1, activation = finalactivation)
    summary(model)
  } else if (numberOfHiddenLayers == 5) {
    model <- keras_model_sequential()
    model %>%
      layer_dense(units = l1.units, activation = activation, input_shape = c(ncol(x_train))) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l2.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l3.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l4.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = l5.units, activation = activation, use_bias = useBias) %>%
      layer_dropout(dropoutRate) %>%
      layer_dense(units = 1, activation = finalactivation)
    summary(model)
  } else {
    print("============== WARNING ==============")
    print("Input value for [numberOfHiddenLayers] must be 0, 1, 2, or 3.")
    print("Since none of the values above are entered, the default is set to 1.")
    print("=====================================")
  } # Done with model


  # Next, compile the model with appropriate loss function, optimizer, and metrics:
  model %>% compile(
    loss = loss,
    optimizer = optimizer,
    metrics = c(loss))

  # Training and Evaluation
  history <- model %>% fit(
    x_train, y_train,
    epochs = epochs,
    batch_size = batch_size,
    validation_split = validation_split
  ); plot(history)

  # Evaluate the model's performance on the test data:
  scores = model %>% evaluate(x_test, y_test)

  # Generate predictions on new data:
  if (forceClassifier == TRUE) {
    y_test_hat <- model %>% predict_proba(x_test)
    y_test_binary <- ifelse(y_test_hat > mean(y_test_hat), 1, 0)
    confusion.matrix <- table(Y_Hat = y_test_binary, Y = y_test)
    test.acc <- sum(diag(confusion.matrix))/sum(confusion.matrix)
    all.error <- plyr::count(y_test - cbind(y_test_binary))
    y_test_eval_matrix <- cbind(
      y_test=y_test,
      y_test_hat=y_test_binary,
      y_test_hat_raw=y_test_hat )

    # AUC/ROC
    if ((num_classes == 2) && (nrow(plyr::count(y_test_hat)) > 1)) {
      AUC_test <- pROC::roc(c(y_test), c(y_test_hat))
    } else {
      AUC_test <- c("Estimate do not have enough levels.")
    }

    # Output
    result <- list(
      Confusion.Matrix = confusion.matrix,
      Confusion.Matrix.Pretty = knitr::kable(confusion.matrix),
      Testing.Accuracy = test.acc,
      All.Types.of.Error = all.error,
      Test_AUC = AUC_test
    )
  } else {
    y_test_hat <- model %>% predict_proba(x_test)
    MSE_test <- mean((y_test - y_test_hat)^2)
    y_test_eval_matrix <- cbind(
      y_test=y_test,
      y_test_hat_raw=y_test_hat )

    # Output
    result <- list(
      MSE_test = MSE_test
    )
  }

  # Return
  return(
    list(
      Model = list(model = model, scores = scores),
      x_train = x_train,
      y_train = y_train,
      x_test = x_test,
      y_test = y_test,
      y_test_hat = y_test_hat,
      y_test_eval_matrix = y_test_eval_matrix,
      Training.Plot = plot(history),
      Result = result
    )
  )
}

## Pull data

In [3]:
# reads time series data
all_confirmed_cases <- covid19.data("ts-confirmed")
all_confirmed_deaths <- covid19.data("ts-deaths")
all_confirmed_recoveries <- covid19.data("ts-recovered")

Data being read from JHU/CCSE repository



~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~ 


Reading data from https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv

Data retrieved on 2021-07-28 14:09:27 || Range of dates on data: 2020-01-22--2021-07-27 | Nbr of records: 279



-------------------------------------------------------------------------------- 


Data being read from JHU/CCSE repository



...

-------------------------------------------------------------------------------- 


Data being read from JHU/CCSE repository



~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~ 


Reading data from https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv

Data retrieved on 2021-07-28 14:09:28 || Range of dates on data: 2020-01-22--2021-07-27 | Nbr of records: 264



-------------------------------------------------------------------------------- 


In [4]:
# Look at how the data is structured
# View(all_confirmed_cases)

In [5]:
indexList <- c()
countryList <- c()

# Get all rows
for (i in rownames(all_confirmed_cases)) {
    # print(c(i, all_confirmed_cases[i, 2]))
    indexList <- c(indexList, i)
    countryList <- c(countryList, all_confirmed_cases[i, 2])
}

country_index_list <- as.data.frame(cbind(indexList, countryList))

# We can see that Italy is index 154, so we are going to  use that
country_index <- 154

country_index_list[country_index, ]

indexList countryList
154 154       Italy

In [6]:
it_confirmed_cases <- all_confirmed_cases[country_index, ]
it_confirmed_deaths <- all_confirmed_deaths[country_index, ]
it_confirmed_recoveries <- all_confirmed_recoveries[country_index, ]

print("Cases:")
View(it_confirmed_cases)
print("Deaths:")
View(it_confirmed_deaths)
print("Recoveries:")
View(it_confirmed_recoveries)

firstCaseDate <- "2020-01-31"

[1] "Cases:"


Province.State Country.Region Lat      Long     2020-01-22 2020-01-23
154                Italy          41.87194 12.56738 0          0         
    2020-01-24 2020-01-25 2020-01-26 2020-01-27 ⋯ 2021-07-18 2021-07-19
154 0          0          0          0          ⋯ 4287458    4289528   
    2021-07-20 2021-07-21 2021-07-22 2021-07-23 2021-07-24 2021-07-25
154 4293083    4297337    4302393    4307535    4312673    4317415   
    2021-07-26 2021-07-27
154 4320530    4325046

[1] "Deaths:"


Province.State Country.Region Lat      Long     2020-01-22 2020-01-23
154                Italy          41.87194 12.56738 0          0         
    2020-01-24 2020-01-25 2020-01-26 2020-01-27 ⋯ 2021-07-18 2021-07-19
154 0          0          0          0          ⋯ 127867     127874    
    2021-07-20 2021-07-21 2021-07-22 2021-07-23 2021-07-24 2021-07-25
154 127884     127905     127920     127937     127942     127949    
    2021-07-26 2021-07-27
154 127971     127995

[1] "Recoveries:"


Province.State Country.Region Lat      Long      2020-01-22 2020-01-23
154                Liberia        6.428055 -9.429499 0          0         
    2020-01-24 2020-01-25 2020-01-26 2020-01-27 ⋯ 2021-07-18 2021-07-19
154 0          0          0          0          ⋯ 2715       2715      
    2021-07-20 2021-07-21 2021-07-22 2021-07-23 2021-07-24 2021-07-25
154 2715       2715       2715       2715       2715       2715      
    2021-07-26 2021-07-27
154 2715       2715

In [7]:
# Find index of first case
firstInfection <- 0

for (i in 1:ncol(it_confirmed_cases)) {
    if (class(it_confirmed_cases[, i]) == 'integer' && it_confirmed_cases[, i] >= 1) {
        print(paste0("Index of the first infection is: ", i, ", Number of infections is: ", it_confirmed_cases[, i]))
        
        firstInfection <- it_confirmed_cases[, i]
        
        break
    }
}

[1] "Index of the first infection is: 14, Number of infections is: 2"


In [8]:
it_confirmed_cases <- t(it_confirmed_cases[, 5:dim(it_confirmed_cases)[2]])
colnames(it_confirmed_cases) <- c("Cases")
it_confirmed_cases <- as.xts(it_confirmed_cases)

In [9]:
it_confirmed_deaths <- t(it_confirmed_deaths[, 5:dim(it_confirmed_deaths)[2]])
colnames(it_confirmed_deaths) <- c("Deaths")
it_confirmed_deaths <- as.xts(it_confirmed_deaths)

In [10]:
it_confirmed_recoveries <- t(it_confirmed_recoveries[, 5:dim(it_confirmed_recoveries)[2]])
colnames(it_confirmed_recoveries) <- c("Recoveries")
it_confirmed_recoveries <- as.xts(it_confirmed_recoveries)

In [11]:
# Since the recoveries in our data are skewed, I'll write a function which computes a pretty good estimate of the recoveries
compute_recoveries <- function(
    cases,
    deaths,
    data_recoveries,
    recovery_time = 14
) {
    estimated_recoveries <- cases - deaths + data_recoveries
    
    return_dataframe <- lag(estimated_recoveries, recovery_time)
    return_dataframe[1:recovery_time] <- 0
    
    return(return_dataframe)
}

In [12]:
compute_deltas <- function(
    dataframe
) {
    new_dataframe <- data.frame(matrix(NA, nrow = nrow(dataframe)))
    
    for (i in 1:ncol(dataframe)) {
        new_dataframe <- cbind(new_dataframe, diff(dataframe[, i]))
    }
    
    return(new_dataframe[, -1])
}

In [13]:
real_data_total <- as.xts(cbind(it_confirmed_cases, it_confirmed_deaths, compute_recoveries(it_confirmed_cases, it_confirmed_deaths, it_confirmed_recoveries)))
colnames(real_data_total) <- c("Cases", "Deaths", "Recoveries")

In [14]:
dygraph(real_data_total)

HTML widgets cannot be represented in plain text (need html)

Covid recoveries are so low because "In order to be considered recovered by the Centers for Disease Control and Prevention, a person must be free of a fever without the help of medication, show improvement in respiratory conditions and receive negative results from two separate tests performed at least 24 hours apart."

In [15]:
real_data_daily <- compute_deltas(real_data_total)

dygraph(real_data_daily)

HTML widgets cannot be represented in plain text (need html)

In [16]:
minmax_normalize <- function(x, na.rm = TRUE) {
    return((x- min(x)) /(max(x)-min(x)))
}

## Testing different models

### Model Agnostic Variables

In [17]:
# Days that I'm analyzing
analysis_days <- 365

# Date list
dates <- seq(as.Date(firstCaseDate), by = "days", length.out = analysis_days)

In [18]:
firstCaseDate

[1] "2020-01-31"

### SIR Model

If $\beta \cdot S_0 - \gamma < 0$, then we have an epidemic, otherwise not.

In our case, with Italy, if $\beta$ is $1.7$, $\gamma$ is $1$ and $S_0$ is $60000000$, then our $R_0$ is $\frac{\beta S_0}{\gamma}$.

By plugging in our numbers we get:

$$\frac{1.7 \cdot 60000}{1} = 102000000$$

Which means that our $R_0$ is way bigger than 0

$$
\begin{eqnarray}
    \frac{dS}{dt} & = & - \beta S I \\
    \frac{dI}{dt} & = & \beta S I - \gamma I \\
    \frac{dR}{dt} & = & \gamma I \\
\end{eqnarray}
$$

In [30]:
# Model inputs

# S: Susceptible (All population)
# I: Infected (Infected)
# R: Recovered (Dead OR Recovered)

susceptible <- 60e+06 # Source: https://www.statista.com/statistics/786485/population-by-gender-in-italy/#:~:text=Population%20in%20Italy%20in%202020%2C%20by%20gender&text=As%20of%20January%202020%2C%2060.2,roughly%2016%20million%20people%20lived.
infected <- firstInfection
recovered <- 0

initial_state_values = c(S = susceptible, I = infected, R = recovered)

# If beta * S_0 - gamma < 0, then we have an epidemic, otherwise not.

# Parameters
# Beta: The effective transmission rate
# Gamma: The effective recovery rate
# R0: (beta * S_0)/gamma

# The beta for covid is estimated to be ranging from 1.5 to 6.68. With median of 2.79. Source: https://www.ncbi.nlm.nih.gov/pmc/articles/PMC7751056/#:~:text=R0%20of%20COVID%2D19,-R0%20of&text=compared%2012%20studies%20published%20from,an%20interquartile%20range%20of%201.16.
# We can simulate this scenario by having our beta as 0.27 and our gamma as 0.1 

# parameters = c(gamma = 0.1, beta = 0.27)
# parameters = c(gamma = 1, beta = 1.7)
parameters = c(gamma = 2, beta = 2.4)

# Time points

time = seq(from = 1,to = analysis_days, by = 1)

# SIR model function 

sir_model <- function(time,state,parameters){
  with(as.list(c(state,parameters)),{
    N = S + I + R
    lambda = beta*(I/N) 
    dS =- lambda*S
    dI = lambda*S - gamma*I
    dR = gamma*I
    
    return(list(c(dS,dI,dR)))
  }
  )
}


#Solving the differential equations
output <- as.data.frame(ode(y = initial_state_values, func = sir_model, parms = parameters, times = time))

out_long = melt(output , id = "time")

colnames(out_long) <- c("Time", "Variable", "Value")

# dim(out_long)

#### SIR Model Graph

In [32]:
Susceptible <- out_long[1:analysis_days, 3]
Infected <- out_long[(analysis_days + 1):(analysis_days*2), 3]
Recovered <- out_long[(analysis_days*2 + 1):(analysis_days*3), 3]

plot_data <- as.data.frame(cbind(Susceptible, Infected, Recovered))
colnames(plot_data) <- c("Susceptbile", "Infected", "Recovered")
rownames(plot_data) <- dates

plot_data <- as.xts(plot_data)

# head(plot_data)

In [33]:
dygraph(plot_data) %>%
    dyAxis("y", label = "People") %>%
    dyAxis("x", label = "Date")

HTML widgets cannot be represented in plain text (need html)

In [22]:
plot_data_daily <- compute_deltas(plot_data)

dygraph(plot_data_daily) %>%
    dyAxis("y", label = "People (Millions)") %>%
    dyAxis("x", label = "Date")

HTML widgets cannot be represented in plain text (need html)

#### SIR Model Comparison

In [23]:
compare_data_sir <- minmax_normalize(plot_data$Recovered)
compare_data_real <- minmax_normalize(real_data_total$Recoveries)

# View(as.xts(cbind(compare_data_real, compare_data_sir)))

dygraph(as.xts(cbind(compare_data_real, compare_data_sir)))

HTML widgets cannot be represented in plain text (need html)

### SEIR Model

In [39]:
# State values:

# 1: Susceptibles
# 2: Exposed, this means infected, but still not infectious
# 3: Infected
# 4: Recovered or Dead

# Parameters:
# Beta: Same as before
# Gamma: Same as before
# Delta: 1/latent period

contact_rate = 2                  # number of contacts per day
transmission_probability = 0.27      # transmission probability
infectious_period = 20                 # infectious period
latent_period = 25                   # latent period

beta_value = contact_rate * transmission_probability
gamma_value = 1 / infectious_period
delta_value = 1 / latent_period

Ro = beta_value / gamma_value

parameter_list = c (beta = beta_value, gamma = gamma_value, delta = delta_value)

# Susceptibles
susceptibles <- 60e+06 - firstInfection # Source: https://www.statista.com/statistics/786485/population-by-gender-in-italy/#:~:text=Population%20in%20Italy%20in%202020%2C%20by%20gender&text=As%20of%20January%202020%2C%2060.2,roughly%2016%20million%20people%20lived.
infected <- firstInfection
recovered <- 0
exposed <- 0

total_pop <- susceptibles + infected + recovered + exposed

initial_values = c (S = susceptibles/total_pop, E = infected/total_pop, I = recovered/total_pop, R = exposed/total_pop)

timepoints <- seq(0, analysis_days, by=1)

SEIR = function (current_timepoint, state_values, parameters) {
  # create state variables (local variables)
  S = state_values [1]        # susceptibles
  E = state_values [2]        # exposed
  I = state_values [3]        # infectious
  R = state_values [4]        # recovered
  
  with ( 
    as.list (parameters),     # variable names within parameters can be used 
         {
           # compute derivatives
           dS = (-beta * S * I)
           dE = (beta * S * I) - (delta * E)
           dI = (delta * E) - (gamma * I)
           dR = (gamma * I)
           
           # combine results
           results = c (dS, dE, dI, dR)
           list (results)
         }
    )
}

output = lsoda(initial_values, timepoints, SEIR, parameter_list)

# head(output)

#### SEIR Model Graph

In [40]:
output <- output[-1, ]

plot_data <- as.data.frame(cbind(output[, 2], output[, 3], output[, 4], output[, 5]))
rownames(plot_data) <- dates

colnames(plot_data) <- c("Susceptible", "Exposed", "Infected", "Recovered")

plot_data <- as.xts(plot_data)

dygraph(plot_data) %>%
    dyAxis("y", label = "People (Percentage)") %>%
    dyAxis("x", label = "Date (Days)")

HTML widgets cannot be represented in plain text (need html)

In [26]:
plot_data_daily <- compute_deltas(plot_data)

dygraph(plot_data_daily) %>%
    dyAxis("y", label = "People (Millions)") %>%
    dyAxis("x", label = "Date")

HTML widgets cannot be represented in plain text (need html)

#### SEIR Model Comparison

In [27]:
compare_data_sir <- minmax_normalize(plot_data$Recovered)
compare_data_real <- minmax_normalize(real_data_total$Recoveries)

# View(as.xts(cbind(compare_data_real, compare_data_sir)))

dygraph(as.xts(cbind(compare_data_real, compare_data_sir)))

HTML widgets cannot be represented in plain text (need html)

### ARIMA Model